In [1]:
import pandas as pd

In [2]:
df = pd.read_csv("Day20_sample.txt", header=None, sep = '\s*(->)\s*', engine = 'python')
df

0   1        2
0  broadcaster  ->  a, b, c
1           %a  ->        b
2           %b  ->        c
3           %c  ->      inv
4         &inv  ->        a

In [3]:
inter = df[2].apply(lambda x : x.split(', '))
df[2] = inter
df

0   1          2
0  broadcaster  ->  [a, b, c]
1           %a  ->        [b]
2           %b  ->        [c]
3           %c  ->      [inv]
4         &inv  ->        [a]

In [4]:
type(df.iloc[2,2])

list

In [5]:
df['type'] = df[0].apply(lambda x : x[0])
df['module'] = df[0].apply(lambda x : x[1:])
df

0   1          2 type      module
0  broadcaster  ->  [a, b, c]    b  roadcaster
1           %a  ->        [b]    %           a
2           %b  ->        [c]    %           b
3           %c  ->      [inv]    %           c
4         &inv  ->        [a]    &         inv

In [6]:
df.loc[df['module'] == 'roadcaster',['module']] = 'broadcaster'
df

0   1          2 type       module
0  broadcaster  ->  [a, b, c]    b  broadcaster
1           %a  ->        [b]    %            a
2           %b  ->        [c]    %            b
3           %c  ->      [inv]    %            c
4         &inv  ->        [a]    &          inv

In [7]:
df = df.drop(columns = 0)
df

1          2 type       module
0  ->  [a, b, c]    b  broadcaster
1  ->        [b]    %            a
2  ->        [c]    %            b
3  ->      [inv]    %            c
4  ->        [a]    &          inv

In [8]:
df.columns

Index([1, 2, 'type', 'module'], dtype='object')

In [9]:
df = df[['type', 'module', 1, 2,]]
df

type       module   1          2
0    b  broadcaster  ->  [a, b, c]
1    %            a  ->        [b]
2    %            b  ->        [c]
3    %            c  ->      [inv]
4    &          inv  ->        [a]

In [10]:
df.loc[df['type'] == 'b', ['type']] = 'button'
df

type       module   1          2
0  button  broadcaster  ->  [a, b, c]
1       %            a  ->        [b]
2       %            b  ->        [c]
3       %            c  ->      [inv]
4       &          inv  ->        [a]

In [11]:
output = None
output == None

True

In [12]:
def flipflop(pulse, state, input=None, output=None):
    if pulse == 'h' or pulse == None:
        #return state, dest_module, pulse
        _state = state
        dest_module = output
        _pulse = None
        return _state, output, _pulse
    if pulse == 'l' and state =='off':
        _state = 'on'
        dest_module = output
        _pulse = 'h'
        return _state, output, _pulse
    if pulse == 'l' and state == 'on':
        _state = 'off'
        dest_module = output
        _pulse = 'l'
        return _state, output, _pulse
    else:
        print(f"no pulse recorded for {module}")

def conjonction(pulse, state, input, output=None):
    remember = state
    print("remember before: ", remember)
    print ('pulse != None ?', pulse != None)
    if pulse != None:
        remember[output] = pulse
        print("remember after: ", remember)    
        if remember.values == ['h'*len(remember)]:
            _state = remember
            dest_module = output
            _pulse = 'l'
            return _state, dest_module, _pulse
        else:
            _state = remember
            dest_module = output
            _pulse = 'h'
            return _state, dest_module, _pulse
    else:
        _state = remember
        dest_module = output
        _pulse = None      
        return _state, dest_module, _pulse

def broadcast(pulse):
    return pulse

In [13]:
#TEST
#flipflop('l','on','a','b')

In [14]:
broadcast('l')

'l'

In [15]:
list_module = list(df['module'])
list_module

['broadcaster', 'a', 'b', 'c', 'inv']

In [16]:
list_dest = list(df[2])
list_dest

[['a', 'b', 'c'], ['b'], ['c'], ['inv'], ['a']]

In [17]:
dict_dest = dict(zip(list_module, list_dest))
dict_dest

{'broadcaster': ['a', 'b', 'c'],
 'a': ['b'],
 'b': ['c'],
 'c': ['inv'],
 'inv': ['a']}

In [18]:
dict_pulse = dict(zip(list_module,[None]*len(list_module)))
dict_pulse

{'broadcaster': None, 'a': None, 'b': None, 'c': None, 'inv': None}

In [19]:
dict_state = dict(zip(list_module,['off']*len(list_module)))
dict_state

{'broadcaster': 'off', 'a': 'off', 'b': 'off', 'c': 'off', 'inv': 'off'}

In [20]:
dict_type = dict(zip(list_module,list(df['type'])))
dict_type

{'broadcaster': 'button', 'a': '%', 'b': '%', 'c': '%', 'inv': '&'}

In [21]:
for module in [module for module in list_module if dict_type[module] == '&']:
    dict_state[module] = dict(zip(dict_dest[module], ['l']*len(dict_dest[module])))
dict_state

{'broadcaster': 'off', 'a': 'off', 'b': 'off', 'c': 'off', 'inv': {'a': 'l'}}

In [22]:
#TEST
#conjonction('l',{'a':'h','b':'h'}, 'a','b')

In [23]:
list_module_off = list_module

In [24]:
list_module_off.remove('broadcaster')
list_module_off

['a', 'b', 'c', 'inv']

In [25]:
[module for module in list_module_off if dict_type[module] == '%']

['a', 'b', 'c']

In [26]:
liste = ['b','a']
not all(liste[i] == 'a' for i in [0,1])

True

In [27]:
dict_dest

{'broadcaster': ['a', 'b', 'c'],
 'a': ['b'],
 'b': ['c'],
 'c': ['inv'],
 'inv': ['a']}

In [28]:
#ORIGINAL
# il envoie les instructions par batch alors que c'est séquentiel !

# Init
l_count = 0
h_count = 0
_dict_state = dict_state.copy()
_dict_pulse = dict_pulse.copy()
#on 'l' push =>
#print('push button number ', push)
#print(f'pulse l sent to ',dict_dest['broadcaster'])
for module in dict_dest['broadcaster']:
    if dict_type[module] == '%' or dict_type[module] == '&' :
        dict_pulse[module] = 'l'
#loop

print('dict_state : ', dict_state)
print('dict_pulse : ', dict_pulse)
# tant que les états des modules ne sont pas tous à off
while not all(dict_state[x] == 'off' for x in [module for module in list_module_off if dict_type[module] == '%']):
    for module in list_module_off:  
        if dict_type[module] == '%':
            print('***************flipflop ',module)
            for dest_modul in dict_dest[module]:
                flipflop_step = flipflop(dict_pulse[module], dict_state[module], input=module, output=dest_modul)
                #current module 
                _dict_state[module] = flipflop_step[0]
                #destination module
                dest_module = flipflop_step[1]#==dict_dest[module][i]
                _dict_pulse[dest_module] = flipflop_step[2]
                print(f'return _state module {_dict_state[module]}, dest_module {dest_module}, _pulse {_dict_pulse[dest_module]}')
                print(f'return state module {dict_state[module]}, dest_module {dest_module}, pulse {dict_pulse[dest_module]}')
                print("_dict_state['inv'] : ", _dict_state['inv'])
                if dict_pulse[dest_module] == 'l':
                    print('l_count before',l_count)
                    l_count += 1
                    print('l_count after',l_count)
                if dict_pulse[dest_module] == 'h':
                    print('h_count before',h_count)
                    h_count += 1
                    print('h_count after',h_count)
        
        if dict_type[module] == '&':
            print('###############conjonction ',module)
            for dest_modul in dict_dest[module]:
                conjonction_step = conjonction(dict_pulse[module], dict_state[module], input=module, output=dest_modul)
                #current module 
                _dict_state[module] = conjonction_step[0]
                #destination module
                dest_module = conjonction_step[1]#==dict_dest[module][i]
                _dict_pulse[dest_module] = conjonction_step[2] 
                print(f'return _state module {_dict_state[module]}, dest_module {dest_module}, _pulse {_dict_pulse[dest_module]}')
                print(f'return state module {dict_state[module]}, dest_module {dest_module}, pulse {dict_pulse[dest_module]}')
                if _dict_pulse[dest_module] == 'l':
                    print('l_count before',l_count)
                    l_count += 1
                    print('l_count after',l_count)
                if _dict_pulse[dest_module] == 'h':
                    print('h_count before',h_count)
                    h_count += 1
                    print('h_count after',h_count)
    dict_state = _dict_state.copy()
    dict_pulse = _dict_pulse.copy()
    print('dict_state : ', dict_state)
    print('dict_pulse : ', dict_pulse)

dict_state :  {'broadcaster': 'off', 'a': 'off', 'b': 'off', 'c': 'off', 'inv': {'a': 'l'}}
dict_pulse :  {'broadcaster': None, 'a': 'l', 'b': 'l', 'c': 'l', 'inv': None}
***************flipflop  a
return _state module on, dest_module b, _pulse h
return state module off, dest_module b, pulse l
_dict_state['inv'] :  {'a': 'l'}
l_count before 0
l_count after 1
***************flipflop  b
return _state module on, dest_module c, _pulse h
return state module off, dest_module c, pulse l
_dict_state['inv'] :  {'a': 'l'}
l_count before 1
l_count after 2
***************flipflop  c
return _state module on, dest_module inv, _pulse h
return state module off, dest_module inv, pulse None
_dict_state['inv'] :  {'a': 'l'}
###############conjonction  inv
remember before:  {'a': 'l'}
pulse != None ? False
return _state module {'a': 'l'}, dest_module a, _pulse None
return state module {'a': 'l'}, dest_module a, pulse l
dict_state :  {'broadcaster': 'off', 'a': 'on', 'b': 'on', 'c': 'on', 'inv': {'a': 'l'}

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



return _state module on, dest_module b, _pulse None
return state module on, dest_module b, pulse None
_dict_state['inv'] :  {'a': 'h'}
***************flipflop  b
return _state module on, dest_module c, _pulse None
return state module on, dest_module c, pulse None
_dict_state['inv'] :  {'a': 'h'}
***************flipflop  c
return _state module on, dest_module inv, _pulse None
return state module on, dest_module inv, pulse None
_dict_state['inv'] :  {'a': 'h'}
###############conjonction  inv
remember before:  {'a': 'h'}
pulse != None ? False
return _state module {'a': 'h'}, dest_module a, _pulse None
return state module {'a': 'h'}, dest_module a, pulse None
dict_state :  {'broadcaster': 'off', 'a': 'on', 'b': 'on', 'c': 'on', 'inv': {'a': 'h'}}
dict_pulse :  {'broadcaster': None, 'a': None, 'b': None, 'c': None, 'inv': None}
***************flipflop  a
return _state module on, dest_module b, _pulse None
return state module on, dest_module b, pulse None
_dict_state['inv'] :  {'a': 'h'}
***

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



{'a': 'h'}
pulse != None ? False
return _state module {'a': 'h'}, dest_module a, _pulse None
return state module {'a': 'h'}, dest_module a, pulse None
dict_state :  {'broadcaster': 'off', 'a': 'on', 'b': 'on', 'c': 'on', 'inv': {'a': 'h'}}
dict_pulse :  {'broadcaster': None, 'a': None, 'b': None, 'c': None, 'inv': None}
***************flipflop  a
return _state module on, dest_module b, _pulse None
return state module on, dest_module b, pulse None
_dict_state['inv'] :  {'a': 'h'}
***************flipflop  b
return _state module on, dest_module c, _pulse None
return state module on, dest_module c, pulse None
_dict_state['inv'] :  {'a': 'h'}
***************flipflop  c
return _state module on, dest_module inv, _pulse None
return state module on, dest_module inv, pulse None
_dict_state['inv'] :  {'a': 'h'}
###############conjonction  inv
remember before:  {'a': 'h'}
pulse != None ? False
return _state module {'a': 'h'}, dest_module a, _pulse None
return state module {'a': 'h'}, dest_module a

KeyboardInterrupt: 

In [ ]:
# il envoie les instructions par batch alors que c'est séquentiel

# Init
l_count = 0
h_count = 0
_dict_state = dict_state.copy()
_dict_pulse = dict_pulse.copy()
#on 'l' push =>
#print('push button number ', push)
#print(f'pulse l sent to ',dict_dest['broadcaster'])
for module in dict_dest['broadcaster']:
    if dict_type[module] == '%' or dict_type[module] == '&' :
        dict_pulse[module] = 'l'
#loop

print('dict_state : ', dict_state)
print('dict_pulse : ', dict_pulse)
# tant que les états des modules ne sont pas tous à off
while not all(dict_state[x] == 'off' for x in [module for module in list_module_off if dict_type[module] == '%']):
    for module in list_module_off:  
        if dict_type[module] == '%':
            print('***************flipflop ',module)
            for dest_modul in dict_dest[module]:
                flipflop_step = flipflop(dict_pulse[module], dict_state[module], input=module, output=dest_modul)
                #current module 
                _dict_state[module] = flipflop_step[0]
                #destination module
                dest_module = flipflop_step[1]#==dict_dest[module][i]
                _dict_pulse[dest_module] = flipflop_step[2]
                print(f'return _state module {_dict_state[module]}, dest_module {dest_module}, _pulse {_dict_pulse[dest_module]}')
                print(f'return state module {dict_state[module]}, dest_module {dest_module}, pulse {dict_pulse[dest_module]}')
                print("_dict_state['inv'] : ", _dict_state['inv'])
                if dict_pulse[dest_module] == 'l':
                    print('l_count before',l_count)
                    l_count += 1
                    print('l_count after',l_count)
                if dict_pulse[dest_module] == 'h':
                    print('h_count before',h_count)
                    h_count += 1
                    print('h_count after',h_count)
        
        if dict_type[module] == '&':
            print('###############conjonction ',module)
            for dest_modul in dict_dest[module]:
                conjonction_step = conjonction(dict_pulse[module], dict_state[module], input=module, output=dest_modul)
                #current module 
                _dict_state[module] = conjonction_step[0]
                #destination module
                dest_module = conjonction_step[1]#==dict_dest[module][i]
                _dict_pulse[dest_module] = conjonction_step[2] 
                print(f'return _state module {_dict_state[module]}, dest_module {dest_module}, _pulse {_dict_pulse[dest_module]}')
                print(f'return state module {dict_state[module]}, dest_module {dest_module}, pulse {dict_pulse[dest_module]}')
                if _dict_pulse[dest_module] == 'l':
                    print('l_count before',l_count)
                    l_count += 1
                    print('l_count after',l_count)
                if _dict_pulse[dest_module] == 'h':
                    print('h_count before',h_count)
                    h_count += 1
                    print('h_count after',h_count)
    dict_state = _dict_state.copy()
    dict_pulse = _dict_pulse.copy()
    print('dict_state : ', dict_state)
    print('dict_pulse : ', dict_pulse)

In [ ]:
l_count*h_count